In [1]:
import os

# 设置文件夹路径和类别名称
folders = [r'C:\Users\bugs_\PycharmProjects\eegProject\data\Test_EEG\HC',
           r'C:\Users\bugs_\PycharmProjects\eegProject\data\Test_EEG\MDD',
           r'C:\Users\bugs_\PycharmProjects\eegProject\data\Test_EEG\BD']
class_names = ['HC', 'MDD', 'BD']

# 创建存储数据集的字典
data_file = {'filename': []}

# 遍历每个类别的文件夹
for folder, class_name in zip(folders, class_names):
    # 获取文件夹中的Clean.mat文件列表
    file_list = os.listdir(folder)
    file_list = [os.path.join(folder, file) for file in file_list if file.endswith('Clean.mat')]

    # 将数据加入到对应的数据集中
    data_file['filename'].extend([(file, class_name) for file in file_list])


In [2]:
import numpy as np
import scipy.io as sio

label_dic = {'HC': 0, 'MDD': 1, "BD": 2}
target_shape = (284, 16, 24000)
X = np.empty(target_shape)
y = {'label': np.empty(284, dtype=int)}

num_merged = 0

for sub, label in data_file['filename']:  # 被试循环

    data = sio.loadmat(sub)
    sample = data['EEG_ECClean']
    eeg_data = sample["data"][0][0][:, 0:24000]
    X[num_merged] = eeg_data
    y['label'][num_merged] = label_dic[label]
    num_merged += 1

In [3]:
from typing import List


def format_adj_matrix_from_adj_list(channel_list: List,
                                    adj_list: List) -> List[List]:
    node_map = {k: i for i, k in enumerate(channel_list)}
    adj_matrix = np.zeros((len(channel_list), len(channel_list)))

    for start_node_name in adj_list:
        if not start_node_name in channel_list:
            continue
        start_node_index = node_map[start_node_name]
        end_node_list = adj_list[start_node_name]

        for end_node_name in end_node_list:
            if not end_node_name in node_map:
                continue
            end_node_index = node_map[end_node_name]
            adj_matrix[start_node_index][end_node_index] = 1

    return adj_matrix.tolist()


EEG_CHANNEL_LIST = ['Fp1', 'Fp2', 'F7', 'F3', 'F4', 'F8', 'T3', 'C3', 'C4', 'T4', 'T5', 'P3', 'P4', 'T6', 'O1', 'O2']

EEG_ADJACENCY_LIST = {
    'Fp1': ['Fp2', 'F7', 'F3'],
    'Fp2': ['Fp1', 'F4', 'F8'],
    'F7': ['Fp1', 'F3', 'T3'],
    'F3': ['Fp1', 'F7', 'F4', 'C3'],
    'F4': ['Fp2', 'F3', 'F8', 'C4'],
    'F8': ['Fp2', 'F4', 'T4'],
    'T3': ['F7', 'C3', 'T5'],
    'C3': ['F3', 'T3', 'C4', 'P3'],
    'C4': ['F4', 'C3', 'T4', 'P4'],
    'T4': ['F8', 'C4', 'T6'],
    'T5': ['T3', 'P3', 'O1'],
    'P3': ['C3', 'T5', 'P4', 'O1'],
    'P4': ['C4', 'P3', 'T6', 'O2'],
    'T6': ['T4', 'P4', 'O2'],
    'O1': ['T5', 'P3', 'O2'],
    'O2': ['P4', 'T6', 'O1'],
}

EEG_ADJACENCY_MATRIX = format_adj_matrix_from_adj_list(EEG_CHANNEL_LIST,
                                                       EEG_ADJACENCY_LIST)
EEG_ADJACENCY_MATRIX

[[0.0,
  1.0,
  1.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [1.0,
  0.0,
  0.0,
  0.0,
  1.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [1.0,
  0.0,
  1.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [0.0,
  1.0,
  0.0,
  1.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.0,
  0.0],
 [0.0,
  0.0,
  0.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0,
  1.0,
  0.0,
  0.0,
  1.0,
  0.0

In [4]:
from torcheeg import transforms
from torcheeg.datasets import NumpyDataset
from torcheeg.transforms.pyg import ToG

dataset = NumpyDataset(X=X,
                       y=y,
                       io_path='./features/DE',
                       offline_transform=transforms.BandDifferentialEntropy(sampling_rate=200, 
                                                                            band_dict={
                                                                              "delta": (1, 4),
                                                                              "theta": (4, 8),
                                                                              "alpha": (8, 13),
                                                                              "beta": (13, 30),
                                                                              "gamma": (30, 44)
                                                                            }),
                       online_transform=ToG(EEG_ADJACENCY_MATRIX),
                       label_transform=transforms.Select('label'),
                       num_worker=4
                       )
print(dataset[0])

[NUMPY]: 100%|██████████| 2/2 [00:58<00:00, 29.50s/it]

Please wait for the writing process to complete...
(Data(edge_index=[2, 70], x=[16, 5], edge_weight=[70]), 0)


In [5]:
from torcheeg.model_selection import KFold

k_fold = KFold(n_splits=5,
               split_path=f'./tmp_out/split_5',
               shuffle=True)

In [6]:
from torch.nn import Linear
import torch
from torch_geometric.nn import GATConv, global_mean_pool
import torch.nn.functional as F


class GNN(torch.nn.Module):
    def __init__(self, in_channels=5, num_layers=3, hid_channels=64, num_classes=3):
        super().__init__()
        self.conv1 = GATConv(in_channels, hid_channels)
        self.convs = torch.nn.ModuleList()
        for _ in range(num_layers - 1):
            self.convs.append(GATConv(hid_channels, hid_channels))
        self.lin1 = Linear(hid_channels, hid_channels)
        self.lin2 = Linear(hid_channels, num_classes)

    def reset_parameters(self):
        self.conv1.reset_parameters()
        for conv in self.convs:
            conv.reset_parameters()
        self.lin1.reset_parameters()
        self.lin2.reset_parameters()

    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        x = F.relu(self.conv1(x, edge_index))
        for conv in self.convs:
            x = F.relu(conv(x, edge_index))
        x = global_mean_pool(x, batch)
        x = F.relu(self.lin1(x))
        x = F.dropout(x, p=0.5, training=self.training)
        x = self.lin2(x)
        return x

In [7]:
model = GNN()
print(model)

GNN(
  (conv1): GATConv(5, 64, heads=1)
  (convs): ModuleList(
    (0-1): 2 x GATConv(64, 64, heads=1)
  )
  (lin1): Linear(in_features=64, out_features=64, bias=True)
  (lin2): Linear(in_features=64, out_features=3, bias=True)
)


In [8]:
from torch import nn

device = "cuda" if torch.cuda.is_available() else "cpu"
loss_fn = nn.CrossEntropyLoss()
loss_fn.to(device)
batch_size = 64

In [9]:
def train(dataloader, model, loss_fn, optimizer):
    global total_train_step
    size = len(dataloader.dataset)
    model.train()
    train_correct = 0
    for batch_idx, batch in enumerate(dataloader):
        X = batch[0].to(device)
        y = batch[1].to(device)

        # Compute prediction error
        pred = model(X)
        loss = loss_fn(pred, y)

        # Backpropagation
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_train_step += 1

        # if batch_idx % 10 == 0:
        loss, current = loss.item(), batch_idx * len(X)
        print(f"loss: {loss:>7f}  [{current:>5d}/{size:>5d}]")
        writer.add_scalar("train_loss", loss, total_train_step)
        train_correct += (pred.argmax(1) == y).type(torch.float).sum().item()
    train_correct /= size
    writer.add_scalar("train_auc", train_correct, total_train_step)
    print(f"Train Error: \n Accuracy: {(100 * train_correct):>0.1f}% ")

def valid(dataloader, model, loss_fn):
    global total_val_step
    size = len(dataloader.dataset)
    num_batches = len(dataloader)

    model.eval()
    val_loss, correct = 0, 0
    with torch.no_grad():
        for batch in dataloader:
            X = batch[0].to(device)
            y = batch[1].to(device)

            pred = model(X)
            val_loss += loss_fn(pred, y).item()
            correct += (pred.argmax(1) == y).type(torch.float).sum().item()
    val_loss /= num_batches
    correct /= size
    # writer.add_scalar("test_avg_loss", val_loss, total_val_step)
    writer.add_scalar("test_auc", correct, total_val_step)
    total_val_step += 1
    print(f"Test Error: \n Accuracy: {(100 * correct):>0.1f}%, Avg loss: {val_loss:>8f} \n")

In [10]:
from torch.utils.tensorboard import SummaryWriter
from torch_geometric.loader import DataLoader

writer = SummaryWriter(r".\log\log_DE5_gnn3_64_drop5_5k_shuffle111_batch64_epoch3000_lr1e-3")
total_train_step = 0
total_val_step = 0

for i, (train_dataset, val_dataset) in enumerate(k_fold.split(dataset)):

    model = GNN().to(device)
    optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)

    train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=True)

    epochs = 3000
    for t in range(epochs):
        print(f"Epoch {t + 1}\n-------------------------------")
        train(train_loader, model, loss_fn, optimizer)
        valid(val_loader, model, loss_fn)
    print("Done!")
writer.close()

Epoch 1
-------------------------------
loss: 1.089444  [    0/  227]
loss: 1.105218  [   64/  227]
loss: 1.054561  [  128/  227]
loss: 1.044974  [  105/  227]
Train Error: 
 Accuracy: 44.9% 
Test Error: 
 Accuracy: 52.6%, Avg loss: 1.046069 

Epoch 2
-------------------------------
loss: 1.048616  [    0/  227]
loss: 1.047053  [   64/  227]
loss: 1.001172  [  128/  227]
loss: 1.019718  [  105/  227]
Train Error: 
 Accuracy: 55.9% 
Test Error: 
 Accuracy: 52.6%, Avg loss: 1.026604 

Epoch 3
-------------------------------
loss: 0.996068  [    0/  227]
loss: 1.030510  [   64/  227]
loss: 1.027813  [  128/  227]
loss: 1.012279  [  105/  227]
Train Error: 
 Accuracy: 54.2% 
Test Error: 
 Accuracy: 52.6%, Avg loss: 1.023273 

Epoch 4
-------------------------------
loss: 1.033406  [    0/  227]
loss: 1.010738  [   64/  227]
loss: 1.004932  [  128/  227]
loss: 1.085792  [  105/  227]
Train Error: 
 Accuracy: 54.2% 
Test Error: 
 Accuracy: 52.6%, Avg loss: 1.028596 

Epoch 5
----------------